### Introducción al Aprendizaje Supervisado


Tomando el DATASET1:

Primero conviene leer todos los puntos, ya que el 3 y el 4 corresponden a un mismo desarrollo.

* 1- Pequeño agregado al tp2: sería deseable conservar en los índices de las filas de la matriz n-samples x n-features un identificador que relacione la fila con la frase original. Ésto sirve para tomar frases testigos y poder ver frases más cercanas por ejemplo. Pueden usar los ids originales de las frases o hacer unos propios. 

* 2- Las matrices conseguidas a partir de tfidf o countvectorizer son muy sparsas. Es deseable probar distintas técnicas de reducción de dimensión. Por ejemplo: sklearn TruncatedSVD u otros. La matriz reducida puede probarse como un componente más en el pipeline de clasificación.

* 3- Podríamos querer detectar en un futuro aquellas frases del usuario con connotación de violencia o violencia de genero. Para ello podemos empezar a definir nuestros datos en las categorías: violencia/no violencia ó violencia de genero/no vdg. En éste punto necesitarán redefinir sus labels según el objetivo buscado. Se sabe que para análisis de sentimiento Naive Bayes es muy usado. La propuesta es implementar distintos clasificadores, entre ellos uno de tipo Naive Bayes y otros para categorizar los ejemplos o ya sea asignarle a cada frase una probabilidad de pertenecer a una de estas clases. (Antes lea el punto 4)

    * Primero defina bien qué tipo de problema de ML se plantea.

* 4- Como es conocido en ML hay que dividir el dataset de forma aleatoria en conjuntos de entrenamiento, validación y test. Previamente conviene analizar si hay desbalanceo de clases, ya que en tal caso conviene conservar una misma proporción de ejemplos por categoría dentro de cada partición.

    * Entonces, analizar si hay desbalanceo de clases.

    * No hay desbalanceo: train_test_split dividiendo en train, validation, test /Ó cross validation

    * Hay desbalanceo: explorar un stratified samplig. En sklearn esta: sklearn.model_selection.StratifiedKFold (una cross validation)
    
* 5- Elegir las métricas adecuadas para comparar la performance de sus clasificadores y mostrar las matrices de confusión. Comentar resultados.

__Key Words:__
* sklearn TruncatedSVD
* stratified samplig
* Multinomial Naive Bayes

__Links:__
* https://scikit-learn.org/stable/modules/classes.html#module-sklearn.model_selection


In [ ]:
!git clone https://github.com/kunan-sa/asistocovid.git

Cloning into 'asistocovid'...
remote: Enumerating objects: 90, done.
remote: Counting objects: 100% (90/90), done.
remote: Compressing objects: 100% (68/68), done.
remote: Total 90 (delta 42), reused 55 (delta 17), pack-reused 0
Unpacking objects: 100% (90/90), done.


In [ ]:
import pandas as pd
import numpy as np
import seaborn as sns
from sklearn import preprocessing
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.model_selection import StratifiedKFold
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import classification_report
from sklearn import metrics
from sklearn.model_selection import train_test_split
from sklearn.linear_model import SGDClassifier
from sklearn.pipeline import make_pipeline
from sklearn.decomposition import TruncatedSVD
from sklearn.preprocessing import Normalizer
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.tree import DecisionTreeClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from sklearn.model_selection import GridSearchCV




/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [ ]:
from nltk.corpus import stopwords
import nltk
nltk.download('stopwords')
stops = set(stopwords.words('spanish'))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [ ]:

df= pd.read_csv('/content/asistocovid/DatasetAsistocovid.csv')

In [ ]:
df[(df.evento=='user') & (df.texto.str.contains('^/'))]

ID_evento                       ID_conversacion  ...      fecha      hora
19            19  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  25-3-2020  17:25:35
23            23  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  25-3-2020  17:25:43
24            24  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  25-3-2020  17:25:43
28            28  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  25-3-2020  17:25:47
29            29  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  25-3-2020  17:25:47
...          ...                                   ...  ...        ...       ...
23363      23363      53355a50207a472a95593b24152ca12f  ...  10-6-2020   19:52:1
23365      23365      1e275a16149c48aeace9598af9e9c3f4  ...  10-6-2020   20:1:44
23367      23367      b760c1f9917245339119683914b9c701  ...  10-6-2020   20:6:19
23369      23369      21c953e3096d4d2a8efcf9f0ea93ba17  ...  10-6-2020  20:18:15
23377      23377      85913d6328f94070a7cf57ba1c393d7e  ...  10-6-2020   20:42:4

[4765 rows x 8 columns]

In [ ]:
df['tipo']= np.where((df.evento=='user')& (df.texto.str.contains('^/')), 0,1)
df[df.tipo==0]

ID_evento                       ID_conversacion  ...      hora tipo
19            19  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  17:25:35    0
23            23  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  17:25:43    0
24            24  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  17:25:43    0
28            28  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  17:25:47    0
29            29  dd9419e4-e2ce-41ff-a873-45ee155b7332  ...  17:25:47    0
...          ...                                   ...  ...       ...  ...
23363      23363      53355a50207a472a95593b24152ca12f  ...   19:52:1    0
23365      23365      1e275a16149c48aeace9598af9e9c3f4  ...   20:1:44    0
23367      23367      b760c1f9917245339119683914b9c701  ...   20:6:19    0
23369      23369      21c953e3096d4d2a8efcf9f0ea93ba17  ...  20:18:15    0
23377      23377      85913d6328f94070a7cf57ba1c393d7e  ...   20:42:4    0

[4765 rows x 9 columns]

In [ ]:
data= df[(df.evento=='user')&(df.tipo==1)]
data = data[['ID_evento', 'texto', 'categoria']]
data=data.dropna()
data

ID_evento                             texto        categoria
0              0        puedo ir a pasear mi perro      ask_mascota
2              2   como sé si tengo el coronavirus     ask_sintomas
4              4    Puedo ir a visitar otra gente?  ask_aislamiento
6              6         puedo ir al supermercado?     ask_mercados
8              8  están abierto los supermercados?     ask_mercados
...          ...                               ...              ...
23355      23355    Cuantos casos hay en argentina        ask_datos
23357      23357                        Infectados        ask_datos
23371      23371     Cuántos casos hay en Córdoba?        ask_datos
23373      23373          De dónde son esos casos?        ask_datos
23375      23375            Infecrados hoy cordoba        ask_datos

[7769 rows x 3 columns]

In [ ]:
#Removemos las tildes de las palabras
data['texto'] =data.texto.str.normalize('NFKD').str.encode('ascii', errors='ignore').str.decode('utf-8')


In [ ]:
# efinimos un nuevo label 'vdg' como 1 si corresponde a violencia de género y 0 en caso contrario

data['vdg']=np.where(data.categoria.str.contains('violencia'),1,0)
data

ID_evento                             texto        categoria  vdg
0              0        puedo ir a pasear mi perro      ask_mascota    0
2              2   como se si tengo el coronavirus     ask_sintomas    0
4              4    Puedo ir a visitar otra gente?  ask_aislamiento    0
6              6         puedo ir al supermercado?     ask_mercados    0
8              8  estan abierto los supermercados?     ask_mercados    0
...          ...                               ...              ...  ...
23355      23355    Cuantos casos hay en argentina        ask_datos    0
23357      23357                        Infectados        ask_datos    0
23371      23371     Cuantos casos hay en Cordoba?        ask_datos    0
23373      23373          De donde son esos casos?        ask_datos    0
23375      23375            Infecrados hoy cordoba        ask_datos    0

[7769 rows x 4 columns]

In [ ]:
data.vdg.value_counts('%')

0    0.976187
1    0.023813
Name: vdg, dtype: float64

**Nos ecnontramos ante un problema de clasificación binaria: 'violencia de género' - 'no violencia de género'**


Vemos que el 2% de la muestra corresponden a la categoría violencia de género,por lo tanto se encuentra desbalanceado. Este desbalanceo nos indica que la métrica que debemos tomar son 'precision', y 'recall', ya que un clasificador que le asigne a toda la muestra la clase mayoritaria tendría un accuracy del 97% y los costos podrían ser muy grandes.
Como estamos midiendo casos de violencia de género, (al igual que cancer- nocancer), el hecho de que nuestro clasificador incurra en error de tipo falso negativo puede ser grande, por lo que vamos a prestarle especial atención.

In [ ]:
# Seteamos la variable ID_evento para ubicar las frases luego
data= data.set_index('ID_evento')


In [ ]:
#Hacemos el split entre train y test indicando el desbalanceo en el parámetro 'stratify'
X1 = data.texto
y1= data.vdg

X_train, X_test, y_train, y_test = train_test_split(X1, y1, stratify = y1, random_state=42,test_size=.30, shuffle=True)


In [ ]:
#Generamos la clase Predictions para obtener las frases correspondientes a los true-positives, false-positives, false negatives
class Predictions():

  data =  data
  X_test =  X_test

  p = data[data.vdg==1].index
  n =data[data.vdg==0].index

  def __init__(self, y_pred):
    self.y_pred = y_pred
    
    self.h = np.where(self.y_pred==0)
    self.i =np.where(self.y_pred==1)

    self.j=  X_test.iloc[self.i].index
    self.k = X_test.iloc[self.h].index

    self.fp= set(self.j)- set(self.p)
    self.fp= list(self.fp)
    self.fp =data.loc[self.fp]

    
    self.tp= list(set(self.j) & set(self.p))
    self.tp = data.loc[self.tp]

    self.fn = list(set(self.k) & set(self.p))
    self.fn = data.loc[self.fn]



## Multinomial Naive Bayes

In [ ]:
text_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops, max_df=0.90)),
                    ('clf', MultinomialNB()),
 ])
parameters = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
              'clf__fit_prior':(True, False),
               'clf__alpha': (1e-2, 1e-3),
 }


gs_clf = GridSearchCV(text_clf, parameters, n_jobs=-1,cv=3, scoring='f1')
gs_clf = gs_clf.fit(X_train,y_train)

y_pred= gs_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))
print(metrics.confusion_matrix(y_test, y_pred))

pred= Predictions(y_pred)

              precision    recall  f1-score   support

           0       0.99      0.99      0.99      2275
           1       0.57      0.52      0.54        56

    accuracy                           0.98      2331
   macro avg       0.78      0.75      0.77      2331
weighted avg       0.98      0.98      0.98      2331

[[2253   22]
 [  27   29]]


In [ ]:
pred.fn

texto  ... vdg
ID_evento                                                     ...    
6528                                            estoy triste  ...   1
13827                                               Aburrido  ...   1
11779                                      no me siento bien  ...   1
16005                                              me aburro  ...   1
14473                                 De cuanto es la multa?  ...   1
15506                                                 Cerrar  ...   1
19486                          mi marido es violento conmigo  ...   1
16035                           provincis con mayor contagio  ...   1
15023              Hay alguna linea de atencion psicologica?  ...   1
8371                                          me discriminan  ...   1
9909                                        me pica la nariz  ...   1
7095                                                 alcohol  ...   1
16185                                         estoy aburrido  ...   1
13499                    Como es el lavado correcto de manos  ...   1
7099                                                 alcohol  ...   1
3901                                      mi esposo me grita  ...   1
17220                            no leo lo que escribo ayuda  ...   1
20294                            me anguistia esta situacion  ...   1
7754                                            estoy triste  ...   1
17489                                                  Ayuda  ...   1
6107       Me puedo tocar la cara si estoy en mi casa y m...  ...   1
4829                                            Tengo hambre  ...   1
11878                                      no me siento bien  ...   1
11880                                      No me siento bien  ...   1
18033                                          estoy podrido  ...   1
14577      Que hago si estoy en crisis psicologica durant...  ...   1
13942                                         estoy aburrido  ...   1

[27 rows x 3 columns]

Los resultados según matríz de confuisión y las métricas, no resultan muy alentadores, pero observando los falsos negativos que determinó nuestro clasificador, vemos que quizás, los labels no son del todo acertado en algunos casos.

## Descenso de gradiente

In [ ]:
# instanciamos el pipeline con la herramienta de reducción de features TruncatedSVD

svm_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops, max_df=0.90)),
                    ('svd', TruncatedSVD(n_components=50, n_iter=10, random_state=42)),
                    ('clf_svm', SGDClassifier(class_weight='balanced')),
 ])
parameters_svm = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
               'clf_svm__alpha': (1e-2, 1e-3),
               'clf_svm__loss':('hinge', 'log'),
               'clf_svm__eta0':(1e-2, 1e-3)
 }

gs_svm_clf = GridSearchCV(svm_clf, parameters_svm, n_jobs=-1, scoring='f1', cv=3)
gs_svm_clf = gs_svm_clf.fit(X_train, y_train)

y_pred= gs_svm_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))
print(metrics.confusion_matrix(y_test, y_pred))

pred= Predictions(y_pred)

              precision    recall  f1-score   support

           0       1.00      0.56      0.72      2275
           1       0.05      0.98      0.10        56

    accuracy                           0.57      2331
   macro avg       0.53      0.77      0.41      2331
weighted avg       0.98      0.57      0.70      2331

[[1270 1005]
 [   1   55]]


In [ ]:
#Gneramos otra instancia de SVM sin TruncatedSVD
svm_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops, max_df=0.90)),
                    ('clf_svm', SGDClassifier(class_weight='balanced' )),
 ])
parameters_svm = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
               'clf_svm__alpha': (1e-2, 1e-3),
               'clf_svm__loss':('hinge', 'log'),
               'clf_svm__eta0':(1e-2, 1e-3)
}


gs_svm_clf = GridSearchCV(svm_clf, parameters_svm, n_jobs=-1, scoring='f1', cv=3)
gs_svm_clf = gs_svm_clf.fit(X_train, y_train)

y_pred= gs_svm_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))
print(metrics.confusion_matrix(y_test, y_pred))
pred= Predictions(y_pred)

              precision    recall  f1-score   support

           0       0.99      0.98      0.99      2275
           1       0.44      0.68      0.53        56

    accuracy                           0.97      2331
   macro avg       0.71      0.83      0.76      2331
weighted avg       0.98      0.97      0.97      2331

[[2226   49]
 [  18   38]]


In [ ]:
pred.fn #Vemos los falsos negativos que arroja el algoritmo. Vemos un caso que el clasificador omitió y que resulta grave.


texto  ... vdg
ID_evento                                                     ...    
13827                                               Aburrido  ...   1
11779                                      no me siento bien  ...   1
7301                                         Dolor de cabeza  ...   1
11878                                      no me siento bien  ...   1
16005                                              me aburro  ...   1
11880                                      No me siento bien  ...   1
14473                                 De cuanto es la multa?  ...   1
16035                           provincis con mayor contagio  ...   1
3901                                      mi esposo me grita  ...   1
6107       Me puedo tocar la cara si estoy en mi casa y m...  ...   1
15023              Hay alguna linea de atencion psicologica?  ...   1
14577      Que hago si estoy en crisis psicologica durant...  ...   1
15506                                                 Cerrar  ...   1
9909                                        me pica la nariz  ...   1
13942                                         estoy aburrido  ...   1
16185                                         estoy aburrido  ...   1
13499                    Como es el lavado correcto de manos  ...   1
4829                                            Tengo hambre  ...   1

[18 rows x 3 columns]

##Árboles de desición

In [ ]:
tree_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops, max_df=1.0)),
              ('svd', TruncatedSVD(n_components=300, n_iter=10, random_state=42)),
              ('clf_tree', DecisionTreeClassifier(random_state=42)),
 ])
parameters_tree = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
               'clf_tree__criterion': ('gini', 'entropy')

}


gs_tree_clf = GridSearchCV(tree_clf, parameters_tree, n_jobs=-1, scoring='recall')
gs_tree_clf = gs_tree_clf.fit(X_train, y_train)

y_pred= gs_tree_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))
print(metrics.confusion_matrix(y_test, y_pred))
pred= Predictions(y_pred)

              precision    recall  f1-score   support

           0       0.99      0.99      0.99      2275
           1       0.60      0.46      0.53        56

    accuracy                           0.98      2331
   macro avg       0.80      0.73      0.76      2331
weighted avg       0.98      0.98      0.98      2331

[[2258   17]
 [  30   26]]


In [ ]:
pred.fn# vemos varios falsos negativos graves por lo que no resulta satisfactorio


texto  ... vdg
ID_evento                                                     ...    
6528                                            estoy triste  ...   1
13827                                               Aburrido  ...   1
11779                                      no me siento bien  ...   1
7301                                         Dolor de cabeza  ...   1
5638                                   mi marido me maltrata  ...   1
16005                                              me aburro  ...   1
14473                                 De cuanto es la multa?  ...   1
12938                                             Soy hombre  ...   1
15506                                                 Cerrar  ...   1
19486                          mi marido es violento conmigo  ...   1
16035                           provincis con mayor contagio  ...   1
15023              Hay alguna linea de atencion psicologica?  ...   1
8371                                          me discriminan  ...   1
9909                                        me pica la nariz  ...   1
16185                                         estoy aburrido  ...   1
13499                    Como es el lavado correcto de manos  ...   1
3901                                      mi esposo me grita  ...   1
17220                            no leo lo que escribo ayuda  ...   1
20297                             me angustia esta situacion  ...   1
7754                                            estoy triste  ...   1
21712                      si estoy encerrada con mi agresor  ...   1
17489                                                  Ayuda  ...   1
6107       Me puedo tocar la cara si estoy en mi casa y m...  ...   1
4829                                            Tengo hambre  ...   1
14945                             Mi marido no me trata bien  ...   1
11878                                      no me siento bien  ...   1
11880                                      No me siento bien  ...   1
18033                                          estoy podrido  ...   1
14577      Que hago si estoy en crisis psicologica durant...  ...   1
13942                                         estoy aburrido  ...   1

[30 rows x 3 columns]

##SVM

In [ ]:
svc_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops)),
                     ('scaler', StandardScaler(with_mean=False)),
                    ('svc_clf', SVC()),
 ])
parameters_svc = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
               'tfidf__max_features':(300, 100,None),
               'svc_clf__kernel':('rbf', 'sigmoid'),
               'svc_clf__gamma':('scale', 'auto')

}


gs_svc_clf = GridSearchCV(svc_clf, parameters_svc, n_jobs=-1, scoring='f1',cv=3)
gs_svc_clf = gs_svc_clf.fit(X_train, y_train)

y_pred= gs_svc_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))
print(metrics.confusion_matrix(y_test, y_pred))
pred= Predictions(y_pred)

              precision    recall  f1-score   support

           0       0.98      0.99      0.99      2275
           1       0.58      0.32      0.41        56

    accuracy                           0.98      2331
   macro avg       0.78      0.66      0.70      2331
weighted avg       0.97      0.98      0.98      2331

[[2262   13]
 [  38   18]]


In [ ]:
svc_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops)),
                     ('scaler', StandardScaler(with_mean=False)),
                    ('svc_clf', SVC()),
 ])
parameters_svc = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
               'tfidf__max_features':(300, 100,None),
               'svc_clf__kernel':('rbf', 'sigmoid'),
               'svc_clf__gamma':('scale', 'auto')

}


gs_svc_clf = GridSearchCV(svc_clf, parameters_svc, n_jobs=-1, scoring='f1',cv=3)
gs_svc_clf = gs_svc_clf.fit(X_train, y_train)

y_pred= gs_svc_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))
print(metrics.confusion_matrix(y_test, y_pred))
pred= Predictions(y_pred)

              precision    recall  f1-score   support

           0       0.98      0.99      0.99      2275
           1       0.58      0.32      0.41        56

    accuracy                           0.98      2331
   macro avg       0.78      0.66      0.70      2331
weighted avg       0.97      0.98      0.98      2331

[[2262   13]
 [  38   18]]


In [ ]:
pred.fn

texto  ... vdg
ID_evento                                                     ...    
6528                                            estoy triste  ...   1
13827                                               Aburrido  ...   1
11779                                      no me siento bien  ...   1
16388                                  mi pareja me maltrata  ...   1
7301                                         Dolor de cabeza  ...   1
16005                                              me aburro  ...   1
14473                                 De cuanto es la multa?  ...   1
5642       que puedo hacer si estoy encerrada con mi abus...  ...   1
12938                                             Soy hombre  ...   1
15506                                                 Cerrar  ...   1
16035                           provincis con mayor contagio  ...   1
10023                          estoy atrapada con mi agresor  ...   1
15023              Hay alguna linea de atencion psicologica?  ...   1
8371                                          me discriminan  ...   1
9909                                        me pica la nariz  ...   1
7095                                                 alcohol  ...   1
16185                                         estoy aburrido  ...   1
13499                    Como es el lavado correcto de manos  ...   1
7099                                                 alcohol  ...   1
3901                                      mi esposo me grita  ...   1
17220                            no leo lo que escribo ayuda  ...   1
6982                                mi perro se llama goliar  ...   1
20294                            me anguistia esta situacion  ...   1
20297                             me angustia esta situacion  ...   1
1610       que puedo hacer si estoy encerrada con mi abus...  ...   1
7754                                            estoy triste  ...   1
21712                      si estoy encerrada con mi agresor  ...   1
17489                                                  Ayuda  ...   1
9435                                           como me cuida  ...   1
6107       Me puedo tocar la cara si estoy en mi casa y m...  ...   1
4829                                            Tengo hambre  ...   1
14945                             Mi marido no me trata bien  ...   1
10340             Que cepa de coronavirus enferma a humanos?  ...   1
11878                                      no me siento bien  ...   1
11880                                      No me siento bien  ...   1
18033                                          estoy podrido  ...   1
14577      Que hago si estoy en crisis psicologica durant...  ...   1
13942                                         estoy aburrido  ...   1

[38 rows x 3 columns]

# RANDOM FOREST


In [ ]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score

In [ ]:
rf_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops)),
                     ('random_forest', RandomForestClassifier())
 ])


In [ ]:
scores = cross_val_score(rf_clf, X_test, y_test, cv=5, scoring='accuracy')

In [ ]:
scores

array([0.98072805, 0.97854077, 0.97639485, 0.9806867 , 0.98283262])

In [ ]:
print('Accuracy for Tf-Idf & RandomForest : ', scores.mean())

Accuracy for Tf-Idf & RandomForest :  0.979836597402836


In [ ]:
parameters_rf = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
               'tfidf__max_features':(300, 100,None),

}


gs_rf_clf = GridSearchCV(rf_clf, parameters_rf, n_jobs=-1, scoring='f1',cv=3)


In [ ]:
gs_rf_clf = gs_rf_clf.fit(X_train, y_train)

y_pred= gs_rf_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))
print(metrics.confusion_matrix(y_test, y_pred))
pred= Predictions(y_pred)

              precision    recall  f1-score   support

           0       0.99      0.99      0.99      2275
           1       0.69      0.52      0.59        56

    accuracy                           0.98      2331
   macro avg       0.84      0.76      0.79      2331
weighted avg       0.98      0.98      0.98      2331

[[2262   13]
 [  27   29]]


In [ ]:
pred.fn


texto  ... vdg
ID_evento                                                     ...    
6528                                            estoy triste  ...   1
13827                                               Aburrido  ...   1
11779                                      no me siento bien  ...   1
7301                                         Dolor de cabeza  ...   1
5638                                   mi marido me maltrata  ...   1
16005                                              me aburro  ...   1
14473                                 De cuanto es la multa?  ...   1
12938                                             Soy hombre  ...   1
15506                                                 Cerrar  ...   1
16035                           provincis con mayor contagio  ...   1
15023              Hay alguna linea de atencion psicologica?  ...   1
8371                                          me discriminan  ...   1
9909                                        me pica la nariz  ...   1
16185                                         estoy aburrido  ...   1
13499                    Como es el lavado correcto de manos  ...   1
3901                                      mi esposo me grita  ...   1
17220                            no leo lo que escribo ayuda  ...   1
20297                             me angustia esta situacion  ...   1
7754                                            estoy triste  ...   1
17489                                                  Ayuda  ...   1
6107       Me puedo tocar la cara si estoy en mi casa y m...  ...   1
4829                                            Tengo hambre  ...   1
11878                                      no me siento bien  ...   1
11880                                      No me siento bien  ...   1
18033                                          estoy podrido  ...   1
14577      Que hago si estoy en crisis psicologica durant...  ...   1
13942                                         estoy aburrido  ...   1

[27 rows x 3 columns]

# XGBOOST

In [ ]:
import xgboost as xgb

In [ ]:
xgb_clf = Pipeline([('tfidf', TfidfVectorizer(stop_words= stops)),
                     ('xgboost', xgb.XGBClassifier( num_class = 1))
])


In [ ]:
X_test.shape, y_test.shape

((2331,), (2331,))

In [ ]:
scores = cross_val_score(xgb_clf, X_test, y_test, cv=5,scoring='accuracy')


In [ ]:
print('Accuracy for XGBoost Classifier : ', scores.mean())

Accuracy for XGBoost Classifier :  0.9768350626315353


In [ ]:
parameters_xgb = {'tfidf__ngram_range': [(1, 1), (1, 2)],
               'tfidf__use_idf': (True, False),
               'tfidf__max_features':(300, 100,None),
              
}

In [ ]:
parameters_xgb

{'tfidf__max_features': (300, 100, None),
 'tfidf__ngram_range': [(1, 1), (1, 2)],
 'tfidf__use_idf': (True, False)}

In [ ]:

gs_xgb_clf = GridSearchCV(xgb_clf, parameters_xgb, n_jobs=-1,cv=3)


In [ ]:
gs_xgb_clf = gs_xgb_clf.fit(X_train, y_train)

y_pred= gs_xgb_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, y_pred))

print(metrics.confusion_matrix(y_test, y_pred))


              precision    recall  f1-score   support

           0       0.98      1.00      0.99      2275
           1       0.71      0.27      0.39        56

    accuracy                           0.98      2331
   macro avg       0.85      0.63      0.69      2331
weighted avg       0.98      0.98      0.98      2331

[[2269    6]
 [  41   15]]


In [ ]:
pred= Predictions(y_pred)

In [ ]:
%load_ext google.colab.data_table
pred.fn


The google.colab.data_table extension is already loaded. To reload it, use:
  %reload_ext google.colab.data_table


texto  ... vdg
ID_evento                                                     ...    
6528                                            estoy triste  ...   1
13827                                               Aburrido  ...   1
11779                                      no me siento bien  ...   1
16388                                  mi pareja me maltrata  ...   1
5638                                   mi marido me maltrata  ...   1
7301                                         Dolor de cabeza  ...   1
16005                                              me aburro  ...   1
14473                                 De cuanto es la multa?  ...   1
5642       que puedo hacer si estoy encerrada con mi abus...  ...   1
12938                                             Soy hombre  ...   1
15506                                                 Cerrar  ...   1
19486                          mi marido es violento conmigo  ...   1
16035                           provincis con mayor contagio  ...   1
10023                          estoy atrapada con mi agresor  ...   1
15023              Hay alguna linea de atencion psicologica?  ...   1
8371                                          me discriminan  ...   1
9909                                        me pica la nariz  ...   1
7095                                                 alcohol  ...   1
3896                                  mi pareja me trata mal  ...   1
16185                                         estoy aburrido  ...   1
13499                    Como es el lavado correcto de manos  ...   1
7099                                                 alcohol  ...   1
3901                                      mi esposo me grita  ...   1
17220                            no leo lo que escribo ayuda  ...   1
6982                                mi perro se llama goliar  ...   1
20294                            me anguistia esta situacion  ...   1
20297                             me angustia esta situacion  ...   1
1610       que puedo hacer si estoy encerrada con mi abus...  ...   1
7754                                            estoy triste  ...   1
21712                      si estoy encerrada con mi agresor  ...   1
17489                                                  Ayuda  ...   1
9435                                           como me cuida  ...   1
6107       Me puedo tocar la cara si estoy en mi casa y m...  ...   1
4829                                            Tengo hambre  ...   1
14945                             Mi marido no me trata bien  ...   1
10340             Que cepa de coronavirus enferma a humanos?  ...   1
11878                                      no me siento bien  ...   1
11880                                      No me siento bien  ...   1
18033                                          estoy podrido  ...   1
14577      Que hago si estoy en crisis psicologica durant...  ...   1
13942                                         estoy aburrido  ...   1

[41 rows x 3 columns]

In [ ]:
%unload_ext google.colab.data_table